# Ejemplo para el cálculo de costes de construccion en el alcance de estudios soluciones clase I (Estrategia protectora avance en paralelo): Parte 2 - Lectura de los datos de entrada asociados a la descripción del proceso constructivo.

Este ejemplo continuará a partir de los datos temporales guardados al final del apartado [Parte 1 - Lectura de los datos de entrada de la forma en planta.](co_costes_construccion_01_es_c1.ipynb)



De acuerdo con el documento Articulado de la ROM 1.1 la descripción del proceso constructivo
deberá incluir: la disponibilidad de medios para
ejecutar los trabajos necesarios, la disponibilidad de materiales y una organización del proceso
constructivo mediante un organigrama con la secuencia de los trabajos. Para la evaluación del
proceso constructivo del dique se deberán enfrentar las diferentes estrategias a las condiciones
climáticas propagadas a cada uno de los tramos del dique. Se deberá describir la organización del
proceso constructivo en los niveles jerárquicos: dique, tramos, subfases constructivas y unidades
de obra.

## Importación de paquetes de IPython

In [1]:
# hidden
import environment as env
env.initialize()

In [2]:
# Python 2/3 setup 
from __future__ import (absolute_import, division, print_function, unicode_literals)
# from builtins import *

In [3]:
# Juypyter setup

%matplotlib inline
import os
import sys
import pickle
import ast
import pandas as pd
env.pandas_setup()
from IPython.display import HTML

## Carga de variables del apartado anterior

In [4]:
# Getting back the objects:
dir_data = os.path.join(env.data_path, 'construccion', 'estudio_soluciones_clase1', 'var_co_costes_construccion_01_es_c1.pkl')

with open(dir_data) as f:  # Python 3: open(..., 'rb')
    n_tramos, de_planta, hora_acumulada, hora_inicio_tramos, p_invernal, alcance, estrategia, ruta_de, ruta_ds, rep_inmediata = pickle.load(f)

## Importación de paquetes para el ejemplo

In [5]:
from construccion.utils_notebook import lectura_fichero_entrada

from construccion.datos_entrada import datos_entrada_tramo
from construccion.datos_entrada import datos_entrada_fase
from construccion.datos_entrada import rendimientos_y_umbrales_datos_entrada

## Iteración sobre cada tramo
Llegados a este punto la herramienta recorre uno a uno cada uno de los tramo del dique. En primer lugar se leen los datos de entrada asociados a cada tramo para posteriomente verificar el proceso constructivo del mismo. En este ejemplo se considerará un único tramo del dique.

In [6]:
# Se asocia la etiqueta del tramo
n = 'T_0'

## Lectura de los ficheros
En primer lugar se leen los ficheros con los datos de entrada necesarios para la descripción del proceso constructivo y posteriormente se pasa a explicar cada uno de ellos.

De acuerdo con el Documento del Articulado de la ROM 1.1 los datos de entrada necesarios relativos a cada tramo del dique
deberán incluir: una descripción del proceso constructivo, la disponibilidad de medios para
ejecutar los trabajos necesarios, la disponibilidad de materiales y una organización del proceso
constructivo mediante un organigrama con la secuencia de los trabajos

In [7]:
# Lectura de los datos de entrada del tramo a partir de ficheros (clima, organizacion proceso constructivo,
# subfases constructivas etc)
(de_tramo, plan_avance, clima, com_fin_teorico) = datos_entrada_tramo(de_planta, n, hora_inicio_tramos, alcance, estrategia, ruta_de, rep_inmediata)

# Lectura de los datos de entrada de cada subfase: unds de obra, maquinaria, ecuaciones de danno, ecs de coste
# y restricciones
(maquinaria_fases, eq_danno_fases, eq_coste_fases, costes_fase, restricciones_fases) = datos_entrada_fase(de_planta, de_tramo, n, estrategia, alcance, ruta_de)

D:\REPOSITORIO GIT\modelo_construccion_2018\construccion\construccion\ecuaciones_danno.py:38: RuntimeWarning: invalid value encountered in double_scalars
  m = (d_max - d_0) / (x_max - x_0)
D:\REPOSITORIO GIT\modelo_construccion_2018\construccion\construccion\ecuaciones_danno.py:77: RuntimeWarning: invalid value encountered in double_scalars
  m = (c_max - c_min) / (d_max - 0)


## Descripción de los datos de entrada
Los datos de entrada relacionados con la descripción del proceso constructivo se agrupan en:
- Datos relativos a los parámetros constructivos de las diferentes subfases de la obra
- Datos relativos a la organización del proceso constructivo de la obra mediante el cronograma con las fecha de inicio y finalización de los trabajos.
- Un tercer grupo con los datos climáticos propagados al tramo del dique.

### Datos climáticos

Dentro de la carpeta ’clima’ es necesario que haya una carpeta por cada uno de los tramos
que componen el dique con el nombre de la etiqueta del tramo (en este caso únicamente uno). Dentro de cada carpeta se debe
encontrar un fichero denominado ’clima.txt’ con las series temporales históricas propagadas al
emplazamiento de cada uno de los agentes necesarios para realizar la verificación del dique. Las
series temporales se estructurarán por columnas.

La matriz con los datos de clima tendrán un valor de nivel (respecto al NMM), velocidad de viento, altura de ola, periodo pico, dirección media de procedendia del oleaje y dirección media de procedencia del viento para cada hora.

Se muestra a continuación un ejemplo del fichero de clima:
 
 

In [8]:
# Cambio el numero de filas y columnas que se muestran 
env.pandas_setup(10, 50)
display(clima)
# Cambio el numero de filas y columnas a sus valores por defecto
env.pandas_setup()

eta        vv        hs     calado
0       0.930918  1.041786  1.041786  16.930918
1       1.337872  1.060341  1.060341  17.337872
2       1.388591  1.078959  1.078959  17.388591
3       1.096256  1.097630  1.097630  17.096256
4       0.467977  1.113442  1.113442  16.467977
...          ...       ...       ...        ...
175316  0.138936  0.324749  0.324749  16.138936
175317  0.541487  0.324876  0.324876  16.541487
175318  0.882342  0.325003  0.325003  16.882342
175319  0.935548  0.325129  0.325129  16.935548
175320  0.739374  0.325256  0.325256  16.739374

[175321 rows x 4 columns]

### Organización del proceso constructivo (Inicio y final teórico de los trabajos)

Se debe introducir el cronograma con los inicios y finales de cada una subfases constructivas.
La estructura del fichero será la siguiente: Se debe introducir una matriz con tantas columnas
como subfases constructivas se empleen para la construcción del tramo y se deseen verificar. Y
tantas filas como horas dure la fase de construcción del tramo. Para cada subfase (columnas) se
indicará con un 1 las horas en las que la subfase trabaja para ejecutar las obras del tramo y con
un 0 las horas en las que no trabaja. Este fichero se introducirá dentro de la carpeta de organización del proceso constructivo con el nombre de plan_de_avance.txt

Se muestra a continuación un ejemplo del fichero:

In [9]:
r_de = os.path.join(ruta_de, 'organizacion_proceso_constructivo', 'plan_avance.txt') 
data = pd.read_table(r_de, sep=',', quoting=2) 
data

T_0\tT_0\tT_0\tT_0\tT_0\tT_0\tT_0\tT_0\tT_0\tT_0\tT_0
0                        1\t0\t0\t0\t0\t0\t0\t0\t0\t0\t0   
1                        1\t0\t0\t0\t0\t0\t0\t0\t0\t0\t0   
2                        1\t0\t0\t0\t0\t0\t0\t0\t0\t0\t0   
3                        1\t0\t0\t0\t0\t0\t0\t0\t0\t0\t0   
4                        1\t0\t0\t0\t0\t0\t0\t0\t0\t0\t0   
...                                                  ...   
21165                    0\t0\t0\t0\t0\t0\t0\t0\t0\t0\t0   
21166                    0\t0\t0\t0\t0\t0\t0\t0\t0\t0\t0   
21167                    0\t0\t0\t0\t0\t0\t0\t0\t0\t0\t0   
21168                    0\t0\t0\t0\t0\t0\t0\t0\t0\t0\t0   
21169                    0\t0\t0\t0\t0\t0\t0\t0\t0\t0\t0   

[21170 rows x 1 columns]

### Parámetros constructivos de las subfases

De acuerdo con el documento del Articulado de la ROM 1.1 se asignará a cada subfase la
cantidad de obra a realizar (medición a ejecutar), los equipos de producción de las unidades
de obra y el conjunto de modos
principales de fallo en cada una de ellas. Para la descripción de cada unidad de maquinaria
se considerarán: los tiempos de arranque, transporte y colocación de la maquinaria, el número
de horas laborables al día, los rendimientos y los umbrales de operatividad.

Los datos de entrada para este ejemplo se han estructurado del siguiente modo, dentro de la carpeta 'subfases' es necesario que haya una carpeta por cada uno de los tramos que componen el dique con el nombre de la etiqueta del tramo. 

La carpeta correspondiente al tramo deberá contener a su vez cuatro carpetas más un fichero denominado 'subfases.txt'. En total la estructura es:
- Fichero 'subfases.txt'
- Carpeta 'parámetros constructivos'
- Carpeta 'maquinaria'
- Carpeta 'modos de fallo'
- Carpeta 'costes'


#### FICHERO SUBFASES
Este fichero le indica a la herramienta las subfases constructivas empleadas para la construcción del tramo así como el orden de ejecución. En este ejemplo se considera que el tramo T\_0 se construye mediante las siguientes subfases:

- Subfase 0: Dragado
- Subfase 1: Vertido del núcleo de la banqueta
- Subfase 2: Vertido del manto de protección de la banqueta
- Subfase 3: Extracción de material para el enrase de la banqueta
- Subfase 4: Adición de material para el enrase de la banqueta
- Subfase 5: Fabricación de los cajones
- Subfase 6: Preparación de los cajones para el remolque
- Subfase 7: Transporte de los cajones
- Subfase 8: Acopio de los cajones
- Subfase 9: Fondeo de los cajones
- Subfase 10: Relleno de celdas

Se muestra a continuación ejemplo del fichero con las subfases constructivas:


In [10]:
# Cambio el numero de filas y columnas que se muestran 
env.pandas_setup(50, 50)

r_de = os.path.join(ruta_de, 'sub_fases', n, 'sub_fases.txt') 
data = pd.read_table(r_de, sep=',', quoting=2, header=None) 
data

# Cambio el numero de filas y columnas a sus valores por defecto
env.pandas_setup()

#### CARPETA PARAMETRO CONSTRUCTIVOS
Cada fichero, contendrá la etiqueta de la subfase constructiva, el volumen a ejecutar por la subfase, si dicha
subfase es protegida por el avance de alguna de las subfases siguientes (1-afirmativo o 0-negativo), en caso afirmativo la
subfase que la protege y la forma de calcular el rendimiento de la subfase a partir del rendimiento
de las unidades de obra que conforman la subfase.

Se muestra a continuación a modo de ejemplo el fichero con los parámetros constructivos asociados a la subfase del dragado. Para mostrar cualquier otra subfase basta con cambiar el nombre en las lineas de abajo

In [11]:
# Codigo para mostrar el fichero en formato html
r_de = os.path.join(ruta_de, 'sub_fases', n, 'parametros_constructivos', '0_dragado.txt')
content = lectura_fichero_entrada(r_de, 2)
data = pd.read_table(r_de, sep=',', quoting=2)
display(data)

vol_subfase  proteccion_por_subfases_siguientes  \
0_dragado     189000.0                                 1.0   

           subfase_protectora rend_uds_obra  
0_dragado                 1.0           min

Para este ejemplo, se considera que se van a ejecutar 189.000 m3 de dragado a lo largo de
los 500 m de longitud del tramo. Esta subfase se protege a medida que avanza la subfase 1:
vertido del núcleo de la banqueta. Y el rendimiento de la subfase se obtiene como el mínimo de
los rendimientos de la unidades de obra de que conforman la subfase.

#### CARPETA DE MAQUINARIA
Cada fichero contendrá para cada tipo de maquinaria dentro de cada unidad de obra: el número
de máquinas a emplear durante la ejecución de la subfase, el rendimiento unitario de cada
máquina, el tiempo de arranque necesario, el número de horas laborables al día, el número de
días laborables a la semana, el coste de la maquinaria unitario, el coste de la mano de obra
unitario, el coste adicional por retrasos y el umbral de operatividad de la máquina.

Se muestra a continuación a modo de ejemplo el fichero con la maquinaria asociada a la subfase del dragado. Para mostrar cualquier otra subfase basta con cambiar el nombre en las lineas de abajo

In [12]:
# Codigo para la lectura del fichero
r_de = os.path.join(ruta_de, 'sub_fases', n, 'maquinaria', '0_dragado.txt')
data = pd.read_table(r_de, sep=',', quoting=2)
# Extraccion del diccionario interior
data = data.loc['Dragado_med_hidra', 'maquinaria']
# Conversion de string a diccionario
maq = ast.literal_eval(data)
maq

{'draga_Volvox_Iberia_succion_marcha': {'coste_add_unit': 200,
  'coste_mano_obra_unit': 700,
  'coste_maq_unit': 700,
  'dia_lab_sem': 6,
  'h_lab_dia': 24,
  'num': 1,
  'rend_unit': 306,
  't_arranque': 48,
  'umb_operatividad': {'calado': 5, 'hs': 2.5, 'nivel': 100, 'vv': 100}}}

Para este ejemplo se considera que el dragado se realiza mediante una única unidad de obra con una única draga Volvox Iberia con un rendimiento de 306 $\mathrm{m^3 \, h^{-1}}$, un tiempo de arranque de 48 $\mathrm{h}$, que trabaja durante 24 h al día de forma continua durante 6 días a la semana. El coste de la maquinaria unitario es de 700 $\mathrm{\euro \, h^{-1}}$, el coste de la mano de obra unitario es de 700 $\mathrm{\euro \, h^{-1}}$ y el coste adicional por retrasos es de 200 $\mathrm{\euro \, h^{-1}}$. Los agentes que limitan operatividad de la máquina son el oleaje y el calado. Se considera que la máquina no puede operar con altura de ola superiores a 2.5 m ni con calados inferiores a los 5 m. El resto de agentes no afectan al funcionamiento de la máquina y por eso se les pone un valor de 100 para que no sean considerados por la herramienta.

#### CARPETA MODOS DE FALLO
Cada fichero contendrá los datos relativos al modo de fallo principal de la subfase constructiva. Los modos de fallo deberán referirse siempre a fallo traducibles en un daño en la sección transversal de la subfase del tramo debidos a un agente principal. Los parámetros a introducir son: etiqueta del modo de fallo principal, etiqueta de la variable responsable de producir el daño, forma de la ecuación de daño (lineal, exponencial, archivo), valor de $x_0$ (valor de la variable correspondiente con el inicio de avería de la subfase), valor de $x_{max}$ (valor de la variable responsable de la pérdida total de la sección trasversal de la subfase), $d_0$ (valor del daño correspondiente al inicio de avería y a un valor de la variable igual a $x_0$), $d_max$ (valor del daño correspondiente a la pérdida total de la sección transversal de la subfase y a un valor de la variable igual a $x_{max}$), nombre del archivo de la ecuación de daño, forma de la ecuación de coste debido a las pérdidas (lineal, exponencial o archivo), valor de $c_{min}$ (valor del coste de las pérdidas asociado con el inicio de avería en la sección trasversal de la subfase), valor de $c_{max}$ (valor del coste asociado a la pérdida total de la sección trasversal de la subfase) y nombre del archivo de la ecuación de coste.

Se muestra a continuación a modo de ejemplo el fichero asociada a la subfase del dragado. Para mostrar cualquier otra subfase basta con cambiar el nombre en las lineas de abajo



In [13]:
# Cambio el numero de filas y columnas que se muestran 
env.pandas_setup(50, 50)

# Codigo para mostrar el fichero en formato html
r_de = os.path.join(ruta_de, 'sub_fases', n, 'modos_fallo', '0_dragado.txt')
content = lectura_fichero_entrada(r_de, 2)
data = pd.read_table(r_de, sep=',', quoting=2)
display(data)

# Devuelvo el numero de filas y columnas por defecto
env.pandas_setup()

modo_fallo_ppal agente ecuacion_danno  x_0  x_max  d_0  d_max  \
0    aterramiento     hs         lineal  1.0    4.0  0.0  378.0   

   archivo_dannos ecuacion_coste  c_min   c_max  archivo_costes  
0             NaN         lineal    0.0  2290.0             NaN

Para este ejemplo se considera que el modo de fallo principal para la subfase de dragado es el aterramiento de la subfase. La variable del agente principal responsable de producir daño es 'hs' (la altura de ola significante). La forma de la ecuación de daño es lineal, en donde el valor de $x_0$ es igual a 1 m y el valor de $x_max$ es igual a 4 m y los valores de $d_0$ y $d_max$ son 0 y 378 $\mathrm{m^3 \, m^{-1}}$ respectivamente. El valor de 378 se ha obtenido dividiendo el volumen total de la subfase 189.000 $\mathrm{m^3}$ por la longitud total del tramo, 500 m. De modo que altura de ola iguales o inferiores a 1 m, el daño producido en la subfase es igual a 0, a partir de 1 m hasta los 4 m, el daño crece de forma lineal hasta los 378 $\mathrm{m^3 \, m^{-1}}$ y el coste crece hasta los 2290 $\mathrm{\geneuro \, m^{-1}}$.

#### CARPETA COSTES
Cada fichero contendrá los datos de: costes materiales unitarios, costes de mantenimiento unitarios y costes indirectos relacionados con la subfase constructiva. 

Se muestra a continuación a modo de ejemplo el fichero asociada a la subfase del dragado. Para mostrar cualquier otra subfase basta con cambiar el nombre en las lineas de abajo

In [14]:
# Cambio el numero de filas y columnas que se muestran 
env.pandas_setup(50, 50)

# Codigo para mostrar el fichero en formato html
r_de = os.path.join(ruta_de, 'sub_fases', n, 'costes', '0_dragado.txt')
content = lectura_fichero_entrada(r_de, 2)
data = pd.read_table(r_de, sep=',', quoting=2)
display(data)

# Devuelvo el numero de filas y columnas por defecto
env.pandas_setup()

costes_materiales_unit  coste_mantenimiento  coste_proteccion  \
0                     0.0                  0.0               0.0   

   costes_indirectos  
0                0.1

### Agrupación de los parámetros constructivos de las subfases

In [15]:
# Cambio el numero de filas y columnas que se muestran 
env.pandas_setup(50, 50)


# Calculo de los valores de rendimiento, n. de horas laborables al dia, n. de dias laborables a la semana, tiempos
# de arranque y umbrales de operatividad a partir de los datos de las maquinarias de las unidades de obra y
# asignacion al dataframe de datos del tramo
de_tramo = rendimientos_y_umbrales_datos_entrada(de_tramo, maquinaria_fases, alcance)
de_tramo

# Cambio el numero de filas y columnas que se muestran a su valor por defecto
env.pandas_setup()

## Guardado de variables

In [16]:
# Saving the objects:
dir_data = os.path.join(env.data_path, 'construccion', 'estudio_soluciones_clase1', 'var_co_costes_construccion_02_es_c1.pkl')

with open(dir_data, 'w') as f:  # Python 3: open(..., 'wb')
    pickle.dump([n, de_tramo, plan_avance, clima, com_fin_teorico, 
                 maquinaria_fases, eq_danno_fases, eq_coste_fases, costes_fase, restricciones_fases], f)

Continuar con [Parte 3 - Verificación del proceso constructivo mediante simulación numérica.](co_costes_construccion_03_es_c1.ipynb)